# Build and install the package

First patch `pyo3-polars`:

- Use [this diff](https://github.com/pola-rs/pyo3-polars/compare/main...Magnus167:pyo3-polars:main) to make changes to the `pyo3-polars` package.

Install the package:

```bash
python -m venv .venv

# source .venv/bin/activate
./.venv/Scripts/activate

pip install maturin ipywidgets

maturin develop --release
```


### Import Python packages


In [ ]:
import macrosynergy
import pandas as pd
import numpy as np
import polars as pl
import os

### Import Python bindings - `msyrs`


In [ ]:
import msyrs

In [ ]:
DATA_FOLDER_PATH = "E:/Work/jpmaqs-data"
# DATA_FOLDER_PATH = "C:/Users/PalashTyagi/Code/go-dataquery/jpmaqs-data"
DQ_CLIENT_ID = os.getenv("DQ_CLIENT_ID")
DQ_CLIENT_SECRET = os.getenv("DQ_CLIENT_SECRET")

In [ ]:
import time

nb_start_time = time.time()

In [ ]:
dfpath = f"{DATA_FOLDER_PATH}/data/ADPEMPL_SA_P1M1ML1/USD_ADPEMPL_SA_P1M1ML1.csv"

starttime = time.time()
ldf: pl.DataFrame = msyrs.qdf.load_qdf(dfpath)
print(f"Time taken to load qdf: {time.time() - starttime}")
ldf.head(5)

In [ ]:
cids_dm = "AUD.CAD.CHF.EUR.GBP.JPY.NOK.NZD.SEK.USD".split(".")
cids_em = "CLP.COP.CZK.HUF.IDR.ILS.INR.KRW.MXN.PLN.THB.TRY.TWD.ZAR".split(".")
cids = cids_dm + cids_em
cids_dux = list(set(cids) - set(["IDR", "NZD"]))
ecos = "CPIC_SA_P1M1ML12.CPIC_SJA_P3M3ML3AR.CPIC_SJA_P6M6ML6AR.CPIH_SA_P1M1ML12.CPIH_SJA_P3M3ML3AR.CPIH_SJA_P6M6ML6AR.INFTEFF_NSA.INTRGDP_NSA_P1M1ML12_3MMA.INTRGDPv5Y_NSA_P1M1ML12_3MMA.PCREDITGDP_SJA_D1M1ML12.RGDP_SA_P1Q1QL4_20QMA.RYLDIRS02Y_NSA.RYLDIRS05Y_NSA.PCREDITBN_SJA_P1M1ML12".split(
    "."
)


mkts = "DU02YXR_NSA.DU05YXR_NSA.DU02YXR_VT10.DU05YXR_VT10.EQXR_NSA.EQXR_VT10.FXXR_NSA.FXXR_VT10.FXCRR_NSA.FXTARGETED_NSA.FXUNTRADABLE_NSA".split(
    "."
)
xcats = ecos + mkts

tickers = [f"{c}_{x}" for c in cids for x in xcats]

In [ ]:
# downloaded_df: pl.DataFrame = msyrs.download.download_jpmaqs_indicators_as_df(
#     client_id=DQ_CLIENT_ID,
#     client_secret=DQ_CLIENT_SECRET,
#     tickers=tickers,
# )
# downloaded_df.head(5)

In [ ]:
downloaded_df = None

In [ ]:
# pddf = macrosynergy.download.JPMaQSDownload().download(
#     tickers=tickers,
#     get_catalogue=True,
#     show_progress=True,
#     start_date="1990-01-01",
# )
# pddf = macrosynergy.management.types.QuantamentalDataFrame(pddf)

In [ ]:
starttime = time.time()

big_df: pl.DataFrame = msyrs.qdf.load_qdf_from_download_bank(

    folder_path=DATA_FOLDER_PATH,
    xcats=xcats,

    # folder_path=DATA_FOLDER_PATH, cids=cids

)
print(f"Time taken to load qdf batch: {time.time() - starttime}")


big_df.head(5)

In [ ]:
big_df.estimated_size("mb")

In [ ]:
big_df.to_pandas()

In [ ]:
big_df.to_pandas().memory_usage(deep=True).sum() / 1024**2

In [ ]:
macrosynergy.management.types.QuantamentalDataFrame(big_df.to_pandas())

In [ ]:
macrosynergy.management.types.QuantamentalDataFrame(big_df.to_pandas()).memory_usage(
    deep=True
).sum() / 1024**2

In [ ]:
sel_cids = ["USD", "EUR", "GBP", "AUD", "CAD"]
start = "1990-01-01"

In [ ]:
starttime = time.time()
eq_df = msyrs.qdf.reduce_dataframe(
    df=big_df,
    cids=sel_cids,
    xcats=["EQXR_NSA", "EQXR_VT10"],

    start=start,
)
print(f"Time taken to reduce qdf: {time.time() - starttime}")
eq_df

In [ ]:
# starttime = time.time()
# eq_pd_df = pddf.reduce_df(cids=sel_cids, xcats=["EQXR_NSA", "EQXR_VT10"], start=start)
# print(f"Time taken to reduce qdf: {time.time() - starttime}")

In [ ]:
fx_xcats = [xc for xc in xcats if xc.startswith("FX")]
starttime = time.time()

fx_df = msyrs.qdf.reduce_dataframe(
    df=big_df, cids=sel_cids, start=start, xcats=fx_xcats, intersect=True
)
print(f"Time taken to reduce qdf: {time.time() - starttime}")

In [ ]:
# starttime = time.time()
# fx_pd_df = pddf.reduce_df(cids=sel_cids, xcats=fx_xcats, start=start, intersect=True)
# print(f"Time taken to reduce qdf: {time.time() - starttime}")

In [ ]:
starttime = time.time()
new_df: pl.DataFrame = msyrs.qdf.update_dataframe(df=eq_df, df_add=fx_df)
print("Time taken: ", time.time() - starttime)
new_df.head(10)

In [ ]:
# starttime = time.time()
# new_pd_df = pddf.update_df(df_add=eq_pd_df,)
# print("Time taken: ", time.time() - starttime)

In [ ]:
new_df.tail(10)

In [ ]:
# df: polars::prelude::DataFrame,
# xcat: String,
# cids: Option<Vec<String>>,
# lback_periods: Option<usize>,
# lback_method: Option<String>,
# half_life: Option<f64>,
# start: Option<String>,
# end: Option<String>,
# est_freq: Option<String>,
# remove_zeros: Option<bool>,
# postfix: Option<String>,
# nan_tolerance: Option<f64>,

starttime = time.time()
hv = msyrs.panel.historic_vol(
    df=new_df,
    xcat="EQXR_NSA",
    cids=None,
    lback_periods=252,
    lback_method="calendar",
    half_life=None,
    start=None,
    end=None,
    est_freq=None,
    remove_zeros=None,
    postfix="_HV",
    nan_tolerance=None,
)
print(f"Time taken: {time.time() - starttime}")

starttime = time.time()
a = 1 + 5
print("Time taken: ", time.time() - starttime)

In [ ]:
starttime = time.time()
msyrs.qdf.pivot_dataframe_by_ticker(df=new_df).head(10)
print("Time taken: ", time.time() - starttime)

In [ ]:
# new_pd_df = macrosynergy.management.types.QuantamentalDataFrame(new_pd_df)

In [ ]:
# starttime = time.time()
# new_pd_df.to_wide()
# print("Time taken: ", time.time() - starttime)

In [ ]:
end_time = time.time()
print(f"Time taken: {end_time - nb_start_time} seconds")